In [ ]:
from pathlib import Path
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import scipy
from glob import glob
import os

Prior code from mva:

In [ ]:
def read_xy(path: str):
    df = pd.read_csv(path, skipinitialspace=True)
    df['N'] = df.index + 1
    df['r'] = (df.x ** 2 + df.y ** 2) ** 0.5
    df['cr'] = df.r.cummax()
    df['fd'] = np.log(df.N) / np.log(df.cr)
    df['run'] = os.path.splitext(Path(path).name)[0]

    return df.replace([np.inf, -np.inf], np.nan).dropna()


def read_load(load_dir: str, reader=read_xy):
    paths = glob(f'{load_dir}/*.csv')
    return pd.concat([reader(path) for path in paths])


def read_sp_xy(specific_probability_dir: str):
    probability = float(Path(specific_probability_dir).name)
    df = read_load(specific_probability_dir)
    df['probability'] = probability

    return df


def read_sp(sp_dir: str):
    if not Path(sp_dir).exists():
        raise Exception("Root does not exist")

    return pd.concat([read_sp_xy(specific_probability_dir) for specific_probability_dir in glob(f'{sp_dir}/*')])

In [129]:
def convergent_tail_index(series, tol):
    diffs = np.abs(np.ediff1d(series))
    for i in range(0, len(diffs)):
        if np.max(diffs[i:]) <= tol:
            return i

    # No convergence found
    return None


def mean_of_tail(series, tol=0.05):
    tail_index = convergent_tail_index(series, tol)
    if tail_index is None:
        raise Exception("No convergence found.")

    return np.mean(series[tail_index:])

def std_of_tail(series, tol=0.05):
    tail_index = convergent_tail_index(series, tol)
    if tail_index is None:
        raise Exception("No convergence found.")

    return np.std(series[tail_index:])


def fd_stats(dfs):
    fds = [mean_of_tail(df.fd, 0.1) for df in dfs]
    fds_clean = [f for f in fds if f < np.inf]
    return np.mean(fds_clean), np.mean(fds_clean) / np.sqrt(fds_clean.length())

In [ ]:
plt.plot(c_sticking_probability.p, c_sticking_probability.fd_mean)
plt.plot(rust_sticking_probability.p, rust_sticking_probability.fd_mean)
plt.errorbar([1], [1.70], marker='x', yerr=[0.06])
plt.errorbar([1], [1.7311567309540636], marker='o', color='red', yerr=[0.020648406595153657])
plt.legend(["Minimal Alteration", "Generic System", "Theory", "Previous Model"])

In [ ]:
plt.errorbar(c_sticking_probability.p, c_sticking_probability.fd_mean, c_sticking_probability.fd_std, fmt="o")
plt.errorbar(rust_sticking_probability.p, rust_sticking_probability.fd_mean, rust_sticking_probability.fd_std, fmt="o")
plt.legend(["C", "Rust"])

Hmmm even with a different RNG I still get a dip around 0.6, I think theres something hiding there

In [121]:
a = read_sp("/Users/joshuacoles/Developer/checkouts/jc3091/CompB DLA/data-analysis/data/stick-probability")

/Users/joshuacoles/Library/Caches/pypoetry/virtualenvs/data-analysis-B4Au_hWl-py3.10/lib/python3.10/site-packages/pandas/core/arraylike.py:402: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/Users/joshuacoles/Library/Caches/pypoetry/virtualenvs/data-analysis-B4Au_hWl-py3.10/lib/python3.10/site-packages/pandas/core/arraylike.py:402: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/Users/joshuacoles/Library/Caches/pypoetry/virtualenvs/data-analysis-B4Au_hWl-py3.10/lib/python3.10/site-packages/pandas/core/arraylike.py:402: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/Users/joshuacoles/Library/Caches/pypoetry/virtualenvs/data-analysis-B4Au_hWl-py3.10/lib/python3.10/site-packages/pandas/core/arraylike.py:402: RuntimeWarning: divide by zero encountered in log
  result = getattr(ufunc, method)(*inputs, **kwargs)
/Users/joshu

In [122]:
b = a.groupby(['probability', 'run'])

In [130]:
b.agg(fd_mean=('fd', mean_of_tail), fd_std=('fd', std_of_tail))

fd_mean    fd_std
probability run                    
0.01        1    2.131369  0.015747
            10   2.059625  0.022239
            100  2.149102  0.023224
            11   2.080454  0.035170
            12   2.071115  0.040406
...                   ...       ...
1.00        95   1.762406  0.021516
            96   1.752355  0.027155
            97   1.731518  0.028326
            98   1.752705  0.019703
            99   1.716540  0.029909

[10000 rows x 2 columns]

In [124]:
c = b.agg({ 'fd': mean_of_tail })

In [ ]:
d = c.reset_index().groupby('probability').mean('fd').reset_index()

In [ ]:
plt.plot(d.probability, d.fd)

In [ ]:
d.reset_index()